In [1]:

import pandas as pd
from sentence_transformers import SentenceTransformer
from tqdm import tqdm
import numpy as np

In [2]:
ENCODE = False
if ENCODE:
    ifc = pd.read_csv("app/IFC_processed.csv")

    model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

    def read_and_encode(file_name):
        # Read the CSV file
        df = pd.read_csv(file_name)

        sentences = df['text'].tolist()

        # Initialize tqdm for progress tracking
        embeddings = []
        for sentence in tqdm(sentences, desc=f"Encoding {file_name}"):
            
            embedding = model.encode(sentence, convert_to_numpy=True)
            embeddings.append(embedding)

        return np.array(embeddings)

    def save_embeddings(embeddings, file_name):
        # Save the embeddings to a file
        np.save(file_name, embeddings)

    # Process and save embeddings for each file
    embeddings_ifc = read_and_encode('ifc.csv')
    save_embeddings(embeddings_ifc, 'embeddings_ifc_en.npy')

    embeddings_ebkp = read_and_encode('ebkp.csv')
    save_embeddings(embeddings_ebkp, 'embeddings_ebkp_en.npy')

    embeddings_mf = read_and_encode('mf.csv')
    save_embeddings(embeddings_mf, 'embeddings_mf_en.npy')

    embeddings_uni = read_and_encode('uni.csv')
    save_embeddings(embeddings_uni, 'embeddings_uni_en.npy')



    import pandas as pd
    from sentence_transformers import SentenceTransformer
    from tqdm import tqdm
    import numpy as np

    # Load the sentence transformer model
    model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')

    def read_and_encode(file_name):
        df = pd.read_csv(file_name)
        sentences = df['text'].tolist()

        embeddings = []
        for sentence in tqdm(sentences, desc=f"Encoding {file_name}"):
            embedding = model.encode(sentence, convert_to_numpy=True)
            embeddings.append(embedding)

        return np.array(embeddings)

    def save_embeddings(embeddings, file_name):
        np.save(file_name, embeddings)

    embeddings_ifc = read_and_encode('ifc.csv')
    save_embeddings(embeddings_ifc, 'embeddings_ifc.npy')

    embeddings_ebkp = read_and_encode('ebkp.csv')
    save_embeddings(embeddings_ebkp, 'embeddings_ebkp.npy')

    embeddings_mf = read_and_encode('mf.csv')
    save_embeddings(embeddings_mf, 'embeddings_mf.npy')

    embeddings_uni = read_and_encode('uni.csv')
    save_embeddings(embeddings_uni, 'embeddings_uni.npy')


In [10]:
from neo4j import GraphDatabase

URI = "neo4j+ssc://d4e7c69a.databases.neo4j.io"
AUTH = ("neo4j", "8gGwVhSx2-ycIPiPGOWejHAhufieq2XOOrkOAizxa1E")
driver = GraphDatabase.driver(URI, auth=AUTH)

def get_components_with_same_name(driver, name):
    with driver.session() as session:  
        query = (
            "MATCH (c:Component {name: $name}) "
            "RETURN c"
        )
        result = session.run(query, name=name)
        components = [record['c'] for record in result]
        return components
    
    

def components_by_user():
    driver = GraphDatabase.driver(URI, auth=AUTH)
    return get_components_with_same_name(driver, "door")


In [82]:
import streamlit as st
import pandas as pd
from io import BytesIO
import ifcopenshell
import ast

def create_ifc_file():
    return ifcopenshell.file()

def safe_eval(value):
    try:
        # Check if the value is the string 'None' and keep it as-is
        if value == 'None':
            return 'None'
        # Safely evaluate the string if it is not already a Python literal
        elif not isinstance(value, (int, float, bool)):
            return ast.literal_eval(value)
        return value
    except (ValueError, SyntaxError):
        # Return the value as-is if it cannot be safely evaluated
        return value

def parse_attributes(dict_):
    # Convert the attribute string to a Python list
    #dict_ = ast.literal_eval(dict_)
    evaluated_dict = {key: safe_eval(value) for key, value in dict_.items()}

    return evaluated_dict



def create_ifc_door(ifc_file, attributes):
    # Creating an IfcDoor entity with some attributes
    item = ifc_file.create_entity(
        attributes["classification"],
        GlobalId=ifcopenshell.guid.new(),  # Generating a new GlobalId
        Name=attributes.get('ProcessItem', None),
        OverallHeight=attributes.get('Height', 0),
        OverallWidth=attributes.get('Width', 0),
    )
    return item


# Streamlit app
def download_button(neo4j_node):
    # Initialize an IFC file
    ifc_file = ifcopenshell.file(schema="IFC4")

    # Attributes from your dictionary safe_eval(dict(neo4j_node))
    # Create an IfcDoor entity with the specified attributes
    item = safe_eval(dict(neo4j_node))
    create_ifc_door(ifc_file, item)

    # Output the IFC file to a file on disk
    file_path = 'simple.ifc'
    ifc_file.write(file_path)

    print(f"IFC file written to {file_path}")



In [85]:
import ifcopenshell

def safe_eval(value):
    try:
        # Check if the value is the string 'None' and keep it as-is
        if value == 'None':
            return 'None'
        # Safely evaluate the string if it is not already a Python literal
        elif not isinstance(value, (int, float, bool)):
            return ast.literal_eval(value)
        return value
    except (ValueError, SyntaxError):
        # Return the value as-is if it cannot be safely evaluated
        return value

def parse_attributes(dict_):
    # Convert the attribute string to a Python list
    #dict_ = ast.literal_eval(dict_)
    evaluated_dict = {key: safe_eval(value) for key, value in dict_.items()}

    return evaluated_dict


def create_pset_door_common(ifc_file, door, properties):
    # Create property values
    property_values = []
    for name, value in properties.items():
        # Determine the type of the property and create accordingly
        if isinstance(value, bool):
            property_value = ifc_file.createIfcBoolean(value)
        elif isinstance(value, (float, int)):
            property_value = ifc_file.createIfcReal(value)
        else:  # Assuming default type is text
            property_value = ifc_file.createIfcText(value)
        
        # Create the property itself
        prop = ifc_file.createIfcPropertySingleValue(Name=name, NominalValue=property_value)
        property_values.append(prop)

    # Create the property set
    pset = ifc_file.createIfcPropertySet(
        GlobalId=ifcopenshell.guid.new(),
        OwnerHistory=None,  # Assuming no owner history
        Name="Pset_DoorCommon",
        Description=None,  # Assuming no description
        HasProperties=property_values
    )

    # Relate the property set to the door
    ifc_file.createIfcRelDefinesByProperties(
        GlobalId=ifcopenshell.guid.new(),
        OwnerHistory=None,  # Assuming no owner history
        RelatedObjects=[door],
        RelatingPropertyDefinition=pset
    )

    return pset
# Initialize an IFC file
ifc_file = ifcopenshell.file(schema="IFC4")

# Create an IfcDoor entity (example)
door = ifc_file.create_entity(
    "IfcDoor",
    GlobalId=ifcopenshell.guid.new(),
    Name="Example Door",
)
components = components_by_user()

res = parse_attributes(dict(components[0]))
# Example properties for Pset_DoorCommon
#properties = {
#    'FireRating': 'None',
#    'IsExternal': True
#}
properties = res['attributes']

# Create and associate Pset_DoorCommon with the door
create_pset_door_common(ifc_file, door, properties)

# Output the IFC file to a file on disk
file_path = 'door_with_pset.ifc'
ifc_file.write(file_path)

print(f"IFC file with Pset_DoorCommon written to {file_path}")


IFC file with Pset_DoorCommon written to door_with_pset.ifc


In [83]:
components = components_by_user()

res = parse_attributes(dict(components[0]))

In [69]:
components = components_by_user()
for component in components:
    print(dict(component))
    download_button(dict(component))

{'name': 'door', 'attributes': '{"ProcessItem": "BARREL", "ProcessPerformance": "None", "AcousticRating": "None", "DurabilityRating": "None", "FireExit": "TRUE", "FireRating": "None", "GlazingAreaFraction": "0", "HandicapAccessible": "TRUE", "HasDrive": "TRUE", "HygrothermalRating": "None", "Infiltration": "0", "IsExternal": "TRUE", "MechanicalLoadRating": "None", "Reference": "None", "SecurityRating": "None", "SelfClosing": "TRUE", "SmokeStop": "TRUE", "Status": "DEMOLISH", "ThermalTransmittance": "0", "WaterTightnessRating": "None", "WindLoadRating": "None", "FillGas": "None", "GlassColour": "None", "GlassThickness1": "0", "GlassThickness2": "0", "GlassThickness3": "0", "IsCoated": "TRUE", "IsLaminated": "TRUE", "IsTempered": "TRUE", "IsWired": "TRUE", "ShadingCoefficient": "0", "SolarAbsorption": "0", "SolarHeatGainTransmittance": "0", "SolarReflectance": "0", "SolarTransmittance": "0", "ThermalTransmittanceSummer": "0", "ThermalTransmittanceWinter": "0", "VisibleLightReflectance": 

In [58]:
import ifcopenshell

def create_ifc_door(ifc_file, attributes):
    # Creating an IfcDoor entity with some attributes
    door = ifc_file.create_entity(
        "IfcDoor",
        GlobalId=ifcopenshell.guid.new(),  # Generating a new GlobalId
        Name=attributes.get('ProcessItem', None),
        OverallHeight=attributes.get('Height', 0),
        OverallWidth=attributes.get('Width', 0),

    )
    return door

# Initialize an IFC file
ifc_file = ifcopenshell.file(schema="IFC4")

# Attributes from your dictionary
attributes = {
    'ProcessItem': 'BARREL',
    'Height': 0,
    'Width': 0
}

# Create an IfcDoor entity with the specified attributes
door = create_ifc_door(ifc_file, attributes)

# Output the IFC file to a file on disk
file_path = 'simple_door.ifc'
ifc_file.write(file_path)

print(f"IFC file written to {file_path}")


IndexError: list index out of range

In [1]:
import pandas as pd
import numpy as np
uni = pd.read_csv("Uniclass2015.csv")

# Fill down the Group, Sub group, and Section columns to propagate the last valid observation forward
uni['Group'] = uni['Group'].fillna(method='ffill')
uni['Sub group'] = uni['Sub group'].fillna(method='ffill')
uni['Section'] = uni['Section'].fillna(method='ffill')

# Define a function to find the parent code
def find_parent(code):
    parts = code.split('_')
    if len(parts) > 1 and parts[0]=="Pr":
        return '_'.join(parts[:-1])
    return np.nan

# Create the Parent column
uni['Parent'] = uni['Code'].apply(find_parent)

# Create the final table
tableuni = uni[['Code', 'Parent', 'Title']]
tableuni.columns = ["Code", "Parent", "Title"]
tableuni = tableuni.dropna().reset_index()
tableuni = tableuni[["Code", "Parent", "Title"]]
tableuni

Code       Parent                                    Title
0              Pr_15           Pr                     Preparatory products
1           Pr_15_31        Pr_15            Formless preparatory products
2        Pr_15_31_04     Pr_15_31  Applied cleaning and treatment products
3     Pr_15_31_04_02  Pr_15_31_04             Acid neutralization products
4     Pr_15_31_04_06  Pr_15_31_04              Biocidal cleaning solutions
...              ...          ...                                      ...
7886  Pr_85_51_34_51  Pr_85_51_34                               Millstones
7887     Pr_85_51_51     Pr_85_51                 Mineral milling products
7888     Pr_85_51_88     Pr_85_51                  Timber milling products
7889        Pr_85_73        Pr_85                         Robotic products
7890           Pr_90           Pr        Soft facility management products

[7891 rows x 3 columns]

In [2]:
from rank_bm25 import BM25Okapi
import pandas as pd
# Your titles from the first set
from nltk.stem import PorterStemmer

# Initialize the lemmatizer
stemmer = PorterStemmer()

# Example list of titles that you would replace with your actual data

# Lemmatize each title
uni = tableuni
ebkp = pd.read_csv("eBKP_processed.csv")

# Tokenize both the titles and the IFC componentsstemmer.stem(word)
tokenized_titles = [[stemmer.stem(word) for word in title.lower().split()] for title in uni.Title]
tokenized_ebkp = [[stemmer.stem(word) for word in m.lower().split()] for m in ebkp.Translated_Text]

# Create a BM25 object with the IFC components
bm25 = BM25Okapi(tokenized_ebkp)
bests = []
for title in tokenized_titles:
    scores = bm25.get_scores(title)
    if sum(scores) > 0:
        best_match_index = scores.argmax()
        bests.append(ebkp.code[best_match_index])
    else:
        bests.append(pd.NA)  # Use "NA" if no relevant match is found

# Create DataFrame for eBKP and Uni mapping
ebkp_uni = pd.DataFrame({
    "eBKP": bests,
    "Code": uni.Code.tolist(),
    "Title": uni.Title.tolist(),
})

ebkp_uni = ebkp_uni.dropna().reset_index()
ebkp_uni = ebkp_uni[["eBKP", "Code", "Title"]]
ebkp_uni

eBKP            Code                                    Title
0     H01.01           Pr_15                     Preparatory products
1     H01.01        Pr_15_31            Formless preparatory products
2     G06.03     Pr_15_31_04  Applied cleaning and treatment products
3     H01.01  Pr_15_31_04_02             Acid neutralization products
4     G06.03  Pr_15_31_04_06              Biocidal cleaning solutions
...      ...             ...                                      ...
3764  H01.01     Pr_85_51_34                   Grain milling products
3765  H01.01     Pr_85_51_51                 Mineral milling products
3766  H01.01     Pr_85_51_88                  Timber milling products
3767  H01.01        Pr_85_73                         Robotic products
3768  D02.01           Pr_90        Soft facility management products

[3769 rows x 3 columns]

In [3]:
from rank_bm25 import BM25Okapi
import pandas as pd
# Your titles from the first set
from nltk.stem import PorterStemmer

# Initialize the lemmatizer
stemmer = PorterStemmer()

# Example list of titles that you would replace with your actual data

# Lemmatize each title
uni = tableuni
mf = pd.read_csv("MF_processed.csv")

# Tokenize both the titles and the IFC componentsstemmer.stem(word)
tokenized_titles = [[stemmer.stem(word) for word in title.lower().split()] for title in uni.Title]
tokenized_mf = [[stemmer.stem(word) for word in m.lower().split()] for m in mf.label]

# Create a BM25 object with the IFC components
bm25 = BM25Okapi(tokenized_mf)
bests = []
for title in tokenized_titles:
    scores = bm25.get_scores(title)
    if sum(scores) > 0:
        best_match_index = scores.argmax()
        bests.append(mf.code[best_match_index])
    else:
        bests.append(pd.NA)  # Use "NA" if no relevant match is found


mf_uni = pd.DataFrame({
    "MF": bests,
    "Code": uni.Code.tolist(),
    "Title": uni.Title.tolist(),
    })

mf_uni = mf_uni.dropna().reset_index()
mf_uni = mf_uni[["MF", "Code", "Title"]]
mf_uni

MF            Code                                    Title
0     32 12 13           Pr_15                     Preparatory products
1     32 12 13        Pr_15_31            Formless preparatory products
2     07 81 00     Pr_15_31_04  Applied cleaning and treatment products
3     02 52 19  Pr_15_31_04_02             Acid neutralization products
4     01 74 13  Pr_15_31_04_06              Biocidal cleaning solutions
...        ...             ...                                      ...
7516  41 33 53     Pr_85_51_34                   Grain milling products
7517  45 35 00     Pr_85_51_51                 Mineral milling products
7518  41 33 53     Pr_85_51_88                  Timber milling products
7519  41 31 19        Pr_85_73                         Robotic products
7520  27 35 00           Pr_90        Soft facility management products

[7521 rows x 3 columns]

In [4]:
from rank_bm25 import BM25Okapi
import pandas as pd
# Your titles from the first set
from nltk.stem import PorterStemmer

# Initialize the lemmatizer
stemmer = PorterStemmer()

# Example list of titles that you would replace with your actual data

# Lemmatize each title
uni = tableuni
ifc = pd.read_csv("IFC_processed.csv")

# Tokenize both the titles and the IFC componentsstemmer.stem(word)
tokenized_titles = [[stemmer.stem(word) for word in title.lower().split()] for title in uni.Title]
tokenized_ifc = [[stemmer.stem(word) for word in ifc.lower().split()] for ifc in ifc.IFC]

# Create a BM25 object with the IFC components
bm25 = BM25Okapi(tokenized_ifc)
bests = []
for title in tokenized_titles:
    scores = bm25.get_scores(title)
    if sum(scores) > 0:
        best_match_index = scores.argmax()
        bests.append(ifc.raw[best_match_index])
    else:
        bests.append(pd.NA)  # Use "NA" if no relevant match is found

ifc_uni = pd.DataFrame({
    "IFC": bests,
    "Code": uni.Code.tolist(),
    "Title": uni.Title.tolist(),
    })

ifc_uni = ifc_uni.dropna().reset_index()
ifc_uni = ifc_uni[["IFC", "Code", "Title"]]
ifc_uni

IFC            Code                                    Title
0     IfcProduct           Pr_15                     Preparatory products
1     IfcProduct        Pr_15_31            Formless preparatory products
2     IfcProduct     Pr_15_31_04  Applied cleaning and treatment products
3     IfcProduct  Pr_15_31_04_02             Acid neutralization products
4     IfcProduct  Pr_15_31_04_10              Chemical absorbent products
...          ...             ...                                      ...
6333  IfcProduct     Pr_85_51_34                   Grain milling products
6334  IfcProduct     Pr_85_51_51                 Mineral milling products
6335  IfcProduct     Pr_85_51_88                  Timber milling products
6336  IfcProduct        Pr_85_73                         Robotic products
6337  IfcProduct           Pr_90        Soft facility management products

[6338 rows x 3 columns]

In [5]:
table = pd.merge(tableuni, ifc_uni, how='left', on=["Code", "Title"])
table = pd.merge(table, mf_uni, how='left', on=["Code", "Title"])
table = pd.merge(table, ebkp_uni, how='left', on=["Code", "Title"])
table

Code       Parent                                    Title  \
0              Pr_15           Pr                     Preparatory products   
1           Pr_15_31        Pr_15            Formless preparatory products   
2        Pr_15_31_04     Pr_15_31  Applied cleaning and treatment products   
3     Pr_15_31_04_02  Pr_15_31_04             Acid neutralization products   
4     Pr_15_31_04_06  Pr_15_31_04              Biocidal cleaning solutions   
...              ...          ...                                      ...   
7886  Pr_85_51_34_51  Pr_85_51_34                               Millstones   
7887     Pr_85_51_51     Pr_85_51                 Mineral milling products   
7888     Pr_85_51_88     Pr_85_51                  Timber milling products   
7889        Pr_85_73        Pr_85                         Robotic products   
7890           Pr_90           Pr        Soft facility management products   

             IFC        MF    eBKP  
0     IfcProduct  32 12 13  H01.01  
1     IfcProduct  32 12 13  H01.01  
2     IfcProduct  07 81 00  G06.03  
3     IfcProduct  02 52 19  H01.01  
4            NaN  01 74 13  G06.03  
...          ...       ...     ...  
7886         NaN       NaN     NaN  
7887  IfcProduct  45 35 00  H01.01  
7888  IfcProduct  41 33 53  H01.01  
7889  IfcProduct  41 31 19  H01.01  
7890  IfcProduct  27 35 00  D02.01  

[7891 rows x 6 columns]

In [6]:
import pandas as pd
import numpy as np
# Assuming df is your DataFrame with the following columns: 'Uni Code', 'Parent', 'Uni Title', 'IFC', 'MF', 'eBKP'
# Let's say df is already loaded with your data
df = table
# Function to determine the level of hierarchy based on 'Uni Code'
def get_hierarchy_level(uni_code):
    return uni_code.count('_')

# Apply the function to create a new 'Level' column
df['Level'] = df['Code'].apply(get_hierarchy_level)

# Sort the DataFrame by 'Uni Code' to ensure parents are before children
df = df.sort_values(by='Code')

# Find the maximum level for each 'Parent'
max_levels = df.groupby('Parent')['Level'].max()

# Merge the max_levels into the original DataFrame
df = df.merge(max_levels.rename('Max Level'), left_on='Parent', right_index=True)

# Now, fill the 'IFC', 'MF', and 'eBKP' columns only for the lowest level
# Create a mask for rows which are at the lowest level of their branch
max_level = max(df['Level'])

mask = df['Level'] == max_level

df = df[mask]
df.drop(columns=['Level', 'Max Level'], inplace=True)


table = df
table

Code       Parent                               Title  \
3     Pr_15_31_04_02  Pr_15_31_04        Acid neutralization products   
4     Pr_15_31_04_06  Pr_15_31_04         Biocidal cleaning solutions   
5     Pr_15_31_04_10  Pr_15_31_04         Chemical absorbent products   
6     Pr_15_31_04_11  Pr_15_31_04  Chemical cleaning gels and liquids   
7     Pr_15_31_04_12  Pr_15_31_04                  Chemical poultices   
...              ...          ...                                 ...   
7879  Pr_85_50_27_90  Pr_85_50_27                 Transmission chains   
7880  Pr_85_50_27_92  Pr_85_50_27                    Universal joints   
7882  Pr_85_50_39_38  Pr_85_50_39               Hydraulic power units   
7883  Pr_85_50_39_39  Pr_85_50_39                      Hydraulic rams   
7886  Pr_85_51_34_51  Pr_85_51_34                          Millstones   

                                  IFC           MF    eBKP  
3                          IfcProduct     02 52 19  H01.01  
4                                 NaN     01 74 13  G06.03  
5                          IfcProduct     02 52 00  H01.01  
6                   IfcLiquidTerminal     40 24 16  G06.03  
7                                 NaN     02 52 00     NaN  
...                               ...          ...     ...  
7879      IfcMechanicalFastener.CHAIN  35 59 93.13     NaN  
7880  IfcMechanicalFastener.RAILJOINT     07 84 43     NaN  
7882             IfcJunctionBox.POWER     41 24 26  B04.01  
7883    IfcActuator.HYDRAULICACTUATOR     40 47 26     NaN  
7886                              NaN          NaN     NaN  

[7248 rows x 6 columns]

In [122]:
import pandas as pd 
from neo4j import GraphDatabase
import re

URI = "neo4j+ssc://d4e7c69a.databases.neo4j.io"
AUTH = ("neo4j", "8gGwVhSx2-ycIPiPGOWejHAhufieq2XOOrkOAizxa1E")
driver = GraphDatabase.driver(URI, auth=AUTH)

# Function to create Cypher queries from a pandas DataFrame
def create_cypher_queries_from_dataframe(df):
    queries = []
    for _ , row in df.iterrows():
        # Ensure valid Cypher labels for the component node (labels cannot start with a number or contain special characters)
        component_label = row['Code'].replace(' ', '_').replace('.', '_')

        # Create the main component node
        title = re.sub(r'[^\w\s]', '', row['Title'])
        query = f"MERGE (component:{component_label} {{name: $title}}) "
        params = {'component_label': component_label, 'title': title }

        # Add relationship to parent if it exists
        if pd.notna(row['Parent']):
            # Ensure valid Cypher labels for the parent node
            parent_label = 'P' + row['Parent'].replace(' ', '_').replace('.', '_')
            params['parent_label'] = parent_label

            parent_query = (
                f" MERGE (parent:{parent_label} {{name: $parent_label}})"
                " MERGE (component)-[:IS_A]->(parent) "
            )
            query += parent_query

        for relation, label in [('Parent', 'parent'), ('IFC', ''), ('MF', 'C'), ('eBKP', 'B_')]:
            if pd.notna(row[relation]):
                rel_label = label + row[relation].replace(' ', '_').replace('.', '_')
                # Modify this part for the specific existing node relationship
                query += f"MATCH (existing:{rel_label} {{name: '{rel_label}'}}) "
                query += "MERGE (component)<-[:RELATED]->(existing) "

                params[f"{label}_name"] = row[relation]

        """        # Add relationship to IFC component if it exists
        if pd.notna(row['IFC']):
            ifc_label = 'Ifc_' + row['IFC'].replace(' ', '_').replace('.', '_')
            match_query = (
                "WITH component"
                f"MATCH (i:{ifc_label} {{name: '{row['IFC']}'}})" 
                "WITH component, i" 
                "MERGE (component)<-[:RELATED]->(i)"
            )
            query += match_query

        # Add relationship to MF component if it exists
        if pd.notna(row['MF']):
            mf_label = 'C' + row['MF'].replace(' ', '_').replace('.', '_')
            match_query = (
                f"WITH component"
                "MATCH (m:{mf_label} {{name: '{row['IFC']}'}})" 
                "WITH component, m" 
                "MERGE (component)<-[:RELATED]->(m)"
            )
            query += match_query

        # Add relationship to eBKP component if it exists
        if pd.notna(row['eBKP']):
            eBKP_label = 'B_' + row['eBKP'].replace(' ', '_').replace('.', '_')
            match_query = (
                f"WITH component"
                f"MATCH (e:{eBKP_label} {{name: '{row['IFC']}'}})" 
                "WITH component, e" 
                "MERGE (component)<-[:RELATED]->(e)"
            )
            query += match_query"""
        queries.append({'query': query, 'params': params})
    return queries


# Create queries from DataFrame
queries = create_cypher_queries_from_dataframe(table)


In [132]:
def create_cypher_queries_from_dataframe(df):
    queries = []
    for _, row in df.iterrows():
        # Construct the Cypher query with parameters
        component_label = row['Code'].replace(' ', '_').replace('.', '_')

        query = f"MERGE (component:{component_label} {{name: $title}}) "
        params = {'title': row['Title']}

        # Add relationships to parent, IFC, MF, eBKP components
        for relation, label in [('Parent', ''), ('IFC', ''), ('MF', 'C'), ('eBKP', 'B_')]:
            if pd.notna(row[relation]):
                if relation== "IFC":
                    rel_label = row[relation].replace("Ifc", "Ifc_").replace('.', '_')
                else:
                    rel_label = label + row[relation].replace(' ', '_').replace('.', '_')
                query += f"MERGE (rel_{rel_label}:{rel_label}) "
                query += f"WITH component, rel_{rel_label} "
                query += f"MERGE (component)<-[:RELATED]->(rel_{rel_label}) "
                params[f"{rel_label}"] = rel_label

        queries.append({'query': query, 'params': params})

    return queries
queries = create_cypher_queries_from_dataframe(table)


In [127]:
queries

[{'query': 'MERGE (component:Pr_15_31_04_02 {name: $title}) MERGE (rel_Pr_15_31_04:Pr_15_31_04) WITH component, rel_Pr_15_31_04 MERGE (component)-[:RELATED]->(rel_Pr_15_31_04) MERGE (rel_Ifc__Product:Ifc__Product) WITH component, rel_Ifc__Product MERGE (component)-[:RELATED]->(rel_Ifc__Product) MERGE (rel_C02_52_19:C02_52_19) WITH component, rel_C02_52_19 MERGE (component)-[:RELATED]->(rel_C02_52_19) MERGE (rel_B_H01_01:B_H01_01) WITH component, rel_B_H01_01 MERGE (component)-[:RELATED]->(rel_B_H01_01) ',
  'params': {'title': 'Acid neutralization products',
   'Pr_15_31_04': 'Pr_15_31_04',
   'Ifc__Product': 'Ifc__Product',
   'C02_52_19': 'C02_52_19',
   'B_H01_01': 'B_H01_01'}},
 {'query': 'MERGE (component:Pr_15_31_04_06 {name: $title}) MERGE (rel_Pr_15_31_04:Pr_15_31_04) WITH component, rel_Pr_15_31_04 MERGE (component)-[:RELATED]->(rel_Pr_15_31_04) MERGE (rel_nan:nan) WITH component, rel_nan MERGE (component)-[:RELATED]->(rel_nan) MERGE (rel_C01_74_13:C01_74_13) WITH component, r

In [124]:
component_label = re.sub(r'[^\w\s]', '', "Tennis umpire's stands")
component_label

'Tennis umpires stands'

In [134]:
def run_cypher_query(driver, query, params):
    with driver.session() as session:
        session.run(query, **params)

for query_info in queries:
    print(query_info)
    run_cypher_query(driver, query_info['query'], query_info['params'])

{'query': 'MERGE (component:Pr_15_31_04_02 {name: $title}) MERGE (rel_Pr_15_31_04:Pr_15_31_04) WITH component, rel_Pr_15_31_04 MERGE (component)-[:RELATED]->(rel_Pr_15_31_04) MERGE (rel_Ifc_Product:Ifc_Product) WITH component, rel_Ifc_Product MERGE (component)-[:RELATED]->(rel_Ifc_Product) MERGE (rel_C02_52_19:C02_52_19) WITH component, rel_C02_52_19 MERGE (component)-[:RELATED]->(rel_C02_52_19) MERGE (rel_B_H01_01:B_H01_01) WITH component, rel_B_H01_01 MERGE (component)-[:RELATED]->(rel_B_H01_01) ', 'params': {'title': 'Acid neutralization products', 'Pr_15_31_04': 'Pr_15_31_04', 'Ifc_Product': 'Ifc_Product', 'C02_52_19': 'C02_52_19', 'B_H01_01': 'B_H01_01'}}
{'query': 'MERGE (component:Pr_15_31_04_06 {name: $title}) MERGE (rel_Pr_15_31_04:Pr_15_31_04) WITH component, rel_Pr_15_31_04 MERGE (component)-[:RELATED]->(rel_Pr_15_31_04) MERGE (rel_C01_74_13:C01_74_13) WITH component, rel_C01_74_13 MERGE (component)-[:RELATED]->(rel_C01_74_13) MERGE (rel_B_G06_03:B_G06_03) WITH component, re